In [1]:
import sys 
sys.path.append('../scripts/')
from robot import *
from scipy.stats import multivariate_normal

In [2]:
class Particle: ###particle_obs_update（1行目とobservaiton_updateメソッドだけ）
    def __init__(self, init_pose):
        self.pose = init_pose
        
    def motion_update(self, nu, omega, time, noise_rate_pdf): 
        ns = noise_rate_pdf.rvs()
        pnu = nu + ns[0]*math.sqrt(abs(nu)/time) + ns[1]*math.sqrt(abs(omega)/time)
        pomega = omega + ns[2]*math.sqrt(abs(nu)/time) + ns[3]*math.sqrt(abs(omega)/time)
        self.pose = IdealRobot.state_transition(pnu, pomega, time, self.pose)
        
    def observation_update(self, observation): 
        print(observation)

In [3]:
class Mcl:  ###mcl_obs（1行目とobservaiton_updateメソッドだけ）
    def __init__(self, init_pose, num, motion_noise_stds): 
        self.particles = [Particle(init_pose) for i in range(num)]

        v = motion_noise_stds
        c = np.diag([v["nn"]**2, v["no"]**2, v["on"]**2, v["oo"]**2])
        self.motion_noise_rate_pdf = multivariate_normal(cov=c)
        
    def motion_update(self, nu, omega, time):
        for p in self.particles: p.motion_update(nu, omega, time, self.motion_noise_rate_pdf)
            
    def observation_update(self, observation):   #メソッド追加
        for p in self.particles: p.observation_update(observation)
        
    def draw(self, ax, elems):
        xs = [p.pose[0] for p in self.particles]
        ys = [p.pose[1] for p in self.particles]
        vxs = [math.cos(p.pose[2]) for p in self.particles]
        vys = [math.sin(p.pose[2]) for p in self.particles] 
        elems.append(ax.quiver(xs, ys, vxs, vys, color="blue", alpha=0.5))

In [4]:
class MclAgent(Agent): 
    def __init__(self, time_interval, nu, omega, particle_pose, particle_num=100,\
                motion_noise_stds={"nn":0.19, "no":0.001, "on":0.13, "oo":0.2}): 
        super().__init__(nu, omega)
        self.pf = Mcl(particle_pose, particle_num, motion_noise_stds)
        self.time_interval = time_interval
        
        self.prev_nu = 0.0
        self.prev_omega = 0.0
        
    def decision(self, observation=None):  ###mcl_agent_obs
        self.pf.motion_update(self.prev_nu, self.prev_omega, self.time_interval)
        self.prev_nu, self.prev_omega = self.nu, self.omega
        self.pf.observation_update(observation)   #追加
        return self.nu, self.omega
        
    def draw(self, ax, elems):
        self.pf.draw(ax, elems)

In [6]:
if __name__ == '__main__':  ###mcl_obs_prepare
    time_interval = 0.1 #追加してWorld, MclAgentで利用
    world = World(30, time_interval, debug=True) 

    ### 地図を生成して3つランドマークを追加 ###
    m = Map()                                  
    m.append_landmark(Landmark(-4,2))
    m.append_landmark(Landmark(2,-3))
    m.append_landmark(Landmark(3,3))
    world.append(m)          

    ### ロボットを作る ###
    a = MclAgent(time_interval, 0.2, 10.0/180*math.pi, np.array([0, 0, 0]).T) #MclAgentに
    r = Robot(np.array([0,0,0]).T, sensor=Camera(m), agent=a, color="red")   #初期位置を原点に
    world.append(r)

    world.draw()

[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82637056]), 2)]
[(array([3.95073057, 0.82

[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.59973756, 0.81522095]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.8322612 ]), 2)]
[(array([4.81318281, 0.83

[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77367404]), 2)]
[(array([4.5718635 , 0.77

[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75261599]), 2)]
[(array([3.85460137, 0.75

[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61143664]), 2)]
[(array([3.79336488, 0.61

...

[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.67140578, 1.08083896]), 2)]
[(array([ 4.92183422, -0.27104289]), 1), (array([4.6

[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.59221909, 1.03475615]), 2)]
[(array([ 4.89901696, -0.36552783]), 1), (array([4.5

[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]
[(array([ 5.07068584, -0.43684774]), 1), (array([4.951693 , 0.9341629]), 2)]

[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.50568503, 0.83515704]), 2)]
[(array([ 5.06518977, -0.59129831]), 1), (array([4.5

[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.43076628, 0.7343005 ]), 2)]
[(array([ 4.42264442, -0.68822006]), 1), (array([4.4